In [ ]:
import numpy as np
import pandas as pd
import re
import string
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score

from google.colab import drive
drive.mount('/content/drive')

# قراءة ملف CSV باستخدام Pandas
df = pd.read_csv('/content/drive/MyDrive/train (1).csv')

# Preprocess text data
df['tweet'] = df['tweet'].str.lower()
df['tweet'] = df['tweet'].apply(lambda x: re.sub('@[^\s]+', ' ', x))
df['tweet'] = df['tweet'].apply(lambda x: re.sub('((www\.[^\s]+)|(https?://[^\s]+))', ' ', x))
df['tweet'] = df['tweet'].apply(lambda x: re.sub(f'[{string.punctuation}]', ' ', x))
df['tweet'] = df['tweet'].apply(lambda x: re.sub('[0-9]+', '', x))
df['tweet'] = df['tweet'].apply(lambda x: " ".join(str(x).split()))
df['tweet'] = df['tweet'].apply(lambda x: [w for w in x.split() if w not in stopwords.words('english')])
df['tweet'] = df['tweet'].apply(lambda x: " ".join(x))
df['tweet'] = df['tweet'].apply(lambda x: WordNetLemmatizer().lemmatize(x))

# Fit the bag of words transformer to the text column
bow_transformer = CountVectorizer().fit(df['tweet'])

# Transform the text column to bag of words representation
text_bow = bow_transformer.transform(df['tweet'])

# Apply Tf-Idf transformer to the bag of words representation
tfidf_transformer = TfidfTransformer().fit(text_bow)
text_tfidf = tfidf_transformer.transform(text_bow)

# Split the data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(text_tfidf, df['label'], test_size=0.2, random_state=42)

# Initialize and train the model
model = LogisticRegression()
model.fit(X_train, y_train)

# Predict using the test set
y_pred = model.predict(X_test)

# Calculate accuracy
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy:", accuracy)


Accuracy: 0.677


In [ ]:
import numpy as np
import pandas as pd
import re
import string
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer
from sklearn.model_selection import train_test_split, KFold
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import SVC
from sklearn.naive_bayes import MultinomialNB
from xgboost import XGBClassifier

from google.colab import drive
drive.mount('/content/drive')

# قراءة ملف CSV باستخدام Pandas
df = pd.read_csv('/content/drive/MyDrive/train (1).csv')

# Preprocess text data
df['tweet'] = df['tweet'].str.lower()
df['tweet'] = df['tweet'].apply(lambda x: re.sub('@[^\s]+', ' ', x))
df['tweet'] = df['tweet'].apply(lambda x: re.sub('((www\.[^\s]+)|(https?://[^\s]+))', ' ', x))
df['tweet'] = df['tweet'].apply(lambda x: re.sub(f'[{string.punctuation}]', ' ', x))
df['tweet'] = df['tweet'].apply(lambda x: re.sub('[0-9]+', '', x))
df['tweet'] = df['tweet'].apply(lambda x: " ".join(str(x).split()))
df['tweet'] = df['tweet'].apply(lambda x: [w for w in x.split() if w not in stopwords.words('english')])
df['tweet'] = df['tweet'].apply(lambda x: " ".join(x))
df['tweet'] = df['tweet'].apply(lambda x: WordNetLemmatizer().lemmatize(x))

# Split the data into features and target
X = df['tweet']
y = df['label']

# Initialize models
models = {
    'Logistic Regression': LogisticRegression(),
    'Random Forest': RandomForestClassifier(),
    'Support Vector Machine': SVC(),
    'Multinomial Naive Bayes': MultinomialNB(),
    'XGBoost': XGBClassifier()
}

# Apply K-Fold cross-validation
kf = KFold(n_splits=5, shuffle=True, random_state=42)

for model_name, model in models.items():
    print(f"Training {model_name}:")
    accuracies = []
    for train_index, test_index in kf.split(X):
        X_train, X_test = X.iloc[train_index], X.iloc[test_index]
        y_train, y_test = y.iloc[train_index], y.iloc[test_index]

        # Fit the bag of words transformer to the text column
        bow_transformer = CountVectorizer().fit(X_train)
        # Transform the text column to bag of words representation
        text_bow_train = bow_transformer.transform(X_train)
        text_bow_test = bow_transformer.transform(X_test)

        # Apply Tf-Idf transformer to the bag of words representation
        tfidf_transformer = TfidfTransformer().fit(text_bow_train)
        text_tfidf_train = tfidf_transformer.transform(text_bow_train)
        text_tfidf_test = tfidf_transformer.transform(text_bow_test)

        # Train the model
        model.fit(text_tfidf_train, y_train)

        # Predict using the test set
        y_pred = model.predict(text_tfidf_test)

        # Calculate accuracy
        accuracy = accuracy_score(y_test, y_pred)
        accuracies.append(accuracy)
        print(f"  - Fold accuracy: {accuracy}")

    # Average accuracy across all folds
    avg_accuracy = np.mean(accuracies)
    print(f"{model_name} average accuracy: {avg_accuracy}\n")


FileNotFoundError: [Errno 2] No such file or directory: '/content/drive/MyDrive/train (1).csv'

In [ ]:
import numpy as np
import pandas as pd
import re
import string
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split, KFold, GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score
from imblearn.over_sampling import RandomOverSampler
from sklearn.pipeline import Pipeline

from google.colab import drive
drive.mount('/content/drive')

# قراءة ملف CSV باستخدام Pandas
df = pd.read_csv('/content/drive/MyDrive/train (1).csv')

# Preprocess text column
def preprocess_text(text):
    text = text.lower()
    text = re.sub('@[^\s]+', ' ', text)
    text = re.sub('((www\.[^\s]+)|(https?://[^\s]+))', ' ', text)
    text = re.sub(f'[{string.punctuation}]', ' ', text)
    text = re.sub('[0-9]+', '', text)
    text = " ".join(str(text).split())
    text = [w for w in text.split() if w not in stopwords.words('english')]
    text = " ".join(text)
    text = WordNetLemmatizer().lemmatize(text)
    return text

df['tweet'] = df['tweet'].apply(preprocess_text)

# Split data into features and target
X = df['tweet']
y = df['label']

# Initialize models
models = {
    'Random Forest': RandomForestClassifier(),
    'Logistic Regression': LogisticRegression(),
    'Support Vector Machine': SVC(),
    'Multinomial Naive Bayes': MultinomialNB()
}

# Define hyperparameters grid for each model
param_grid = {
    'Random Forest': {'classifier__n_estimators': [50, 100, 200], 'classifier__max_depth': [None, 10, 20]},
    'Logistic Regression': {'classifier__C': [0.001, 0.01, 0.1, 1, 10, 100]},
    'Support Vector Machine': {'classifier__C': [0.1, 1, 10], 'classifier__gamma': ['scale', 'auto']},
    'Multinomial Naive Bayes': {'classifier__alpha': [0.1, 0.5, 1.0]},
}

# Initialize KFold cross-validator
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Perform hyperparameter tuning for each model
for model_name, model in models.items():
    print(f"Tuning hyperparameters for {model_name}:")

    # Define pipeline with TfidfVectorizer and model
    pipeline = Pipeline([
        ('tfidf', TfidfVectorizer()),
        ('classifier', model)
    ])

    # Perform grid search
    grid_search = GridSearchCV(pipeline, param_grid[model_name], cv=kf, scoring='accuracy', n_jobs=-1)
    grid_search.fit(X, y)

    # Print best parameters and best cross-validation accuracy
    best_params = grid_search.best_params_
    best_score = grid_search.best_score_
    print(f"Best parameters: {best_params}")
    print(f"Best cross-validation accuracy: {best_score}\n")

# Choose the best model
best_model_name = max(models, key=lambda k: grid_search.cv_results_['mean_test_score'][np.argwhere(grid_search.cv_results_['rank_test_score'] == 1)[0][0]])
best_model = grid_search.best_estimator_

# Fit the best model
best_model.fit(X, y)

# Predict using the best model
y_pred = best_model.predict(X)

# Calculate accuracy
accuracy = accuracy_score(y, y_pred)
print("Final Accuracy:", accuracy)


Tuning hyperparameters for Random Forest:
Best parameters: {'classifier__max_depth': None, 'classifier__n_estimators': 100}
Best cross-validation accuracy: 0.6992999999999999

Tuning hyperparameters for Logistic Regression:
Best parameters: {'classifier__C': 10}
Best cross-validation accuracy: 0.7055

Tuning hyperparameters for Support Vector Machine:
Best parameters: {'classifier__C': 10, 'classifier__gamma': 'scale'}
Best cross-validation accuracy: 0.7144999999999999

Tuning hyperparameters for Multinomial Naive Bayes:
Best parameters: {'classifier__alpha': 0.1}
Best cross-validation accuracy: 0.6957

Final Accuracy: 0.9004


In [ ]:
#فصل اعدادات كل موديل
import numpy as np
import pandas as pd
import re
import string
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split, KFold, GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score
from imblearn.over_sampling import RandomOverSampler
from sklearn.pipeline import Pipeline

from google.colab import drive
drive.mount('/content/drive')

# قراءة ملف CSV باستخدام Pandas
df = pd.read_csv('/content/drive/MyDrive/train (1).csv')

# Preprocess text column
def preprocess_text(text):
    text = text.lower()
    text = re.sub('@[^\s]+', ' ', text)
    text = re.sub('((www\.[^\s]+)|(https?://[^\s]+))', ' ', text)
    text = re.sub(f'[{string.punctuation}]', ' ', text)
    text = re.sub('[0-9]+', '', text)
    text = " ".join(str(text).split())
    text = [w for w in text.split() if w not in stopwords.words('english')]
    text = " ".join(text)
    text = WordNetLemmatizer().lemmatize(text)
    return text

df['tweet'] = df['tweet'].apply(preprocess_text)

# Split data into features and target
X = df['tweet']
y = df['label']

# Define hyperparameters grid for Random Forest
param_grid_rf = {
    'classifier__n_estimators': [50, 100, 200],
    'classifier__max_depth': [None, 10, 20]
}

# Define hyperparameters grid for Logistic Regression
param_grid_lr = {
    'classifier__C': [0.001, 0.01, 0.1, 1, 10, 100]
}

# Define hyperparameters grid for Support Vector Machine
param_grid_svm = {
    'classifier__C': [0.1, 1, 10],
    'classifier__gamma': ['scale', 'auto']
}

# Define hyperparameters grid for Multinomial Naive Bayes
param_grid_nb = {
    'classifier__alpha': [0.1, 0.5, 1.0]
}

# Initialize KFold cross-validator
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Random Forest
print("Tuning hyperparameters for Random Forest:")
pipeline_rf = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', RandomForestClassifier())
])
grid_search_rf = GridSearchCV(pipeline_rf, param_grid_rf, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_rf.fit(X, y)
best_params_rf = grid_search_rf.best_params_
best_score_rf = grid_search_rf.best_score_
print(f"Best parameters: {best_params_rf}")
print(f"Best cross-validation accuracy: {best_score_rf}\n")

# Logistic Regression
print("Tuning hyperparameters for Logistic Regression:")
pipeline_lr = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', LogisticRegression())
])
grid_search_lr = GridSearchCV(pipeline_lr, param_grid_lr, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_lr.fit(X, y)
best_params_lr = grid_search_lr.best_params_
best_score_lr = grid_search_lr.best_score_
print(f"Best parameters: {best_params_lr}")
print(f"Best cross-validation accuracy: {best_score_lr}\n")

# Support Vector Machine
print("Tuning hyperparameters for Support Vector Machine:")
pipeline_svm = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', SVC())
])
grid_search_svm = GridSearchCV(pipeline_svm, param_grid_svm, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_svm.fit(X, y)
best_params_svm = grid_search_svm.best_params_
best_score_svm = grid_search_svm.best_score_
print(f"Best parameters: {best_params_svm}")
print(f"Best cross-validation accuracy: {best_score_svm}\n")

# Multinomial Naive Bayes
print("Tuning hyperparameters for Multinomial Naive Bayes:")
pipeline_nb = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', MultinomialNB())
])
grid_search_nb = GridSearchCV(pipeline_nb, param_grid_nb, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_nb.fit(X, y)
best_params_nb = grid_search_nb.best_params_
best_score_nb = grid_search_nb.best_score_
print(f"Best parameters: {best_params_nb}")
print(f"Best cross-validation accuracy: {best_score_nb}\n")

# Choose the best model
best_model_name = max({
    'Random Forest': best_score_rf,
    'Logistic Regression': best_score_lr,
    'Support Vector Machine': best_score_svm,
    'Multinomial Naive Bayes': best_score_nb
}.items(), key=lambda x: x[1])[0]
best_model = None

if best_model_name == 'Random Forest':
    best_model = grid_search_rf.best_estimator_
elif best_model_name == 'Logistic Regression':
    best_model = grid_search_lr.best_estimator_
elif best_model_name == 'Support Vector Machine':
    best_model = grid_search_svm.best_estimator_
elif best_model_name == 'Multinomial Naive Bayes':
    best_model = grid_search_nb.best_estimator_

# Fit the best model
if best_model:
    best_model.fit(X, y)
    # Predict using the best model
    y_pred = best_model.predict(X)
    # Calculate accuracy
    accuracy = accuracy_score(y, y_pred)
    print("Final Accuracy:", accuracy)


Tuning hyperparameters for Random Forest:
Best parameters: {'classifier__max_depth': None, 'classifier__n_estimators': 200}
Best cross-validation accuracy: 0.6977

Tuning hyperparameters for Logistic Regression:
Best parameters: {'classifier__C': 10}
Best cross-validation accuracy: 0.7055

Tuning hyperparameters for Support Vector Machine:
Best parameters: {'classifier__C': 10, 'classifier__gamma': 'scale'}
Best cross-validation accuracy: 0.7144999999999999

Tuning hyperparameters for Multinomial Naive Bayes:
Best parameters: {'classifier__alpha': 0.1}
Best cross-validation accuracy: 0.6957

Final Accuracy: 0.9954


In [ ]:
import numpy as np
import pandas as pd
import re
import string
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split, KFold, GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
import time
from imblearn.over_sampling import RandomOverSampler
from sklearn.pipeline import Pipeline

nltk.download('stopwords')
nltk.download('wordnet')

from google.colab import drive
drive.mount('/content/drive')

# قراءة ملف CSV باستخدام Pandas
df = pd.read_csv('/content/drive/MyDrive/train (1).csv')
df  # إظهار البيانات

# Preprocess text column
def preprocess_text(text):
    text = text.lower()
    text = re.sub('@[^\s]+', ' ', text)
    text = re.sub('((www\.[^\s]+)|(https?://[^\s]+))', ' ', text)
    text = re.sub(f'[{string.punctuation}]', ' ', text)
    text = re.sub('[0-9]+', '', text)
    text = " ".join(str(text).split())
    text = [w for w in text.split() if w not in stopwords.words('english')]
    text = " ".join(text)
    text = WordNetLemmatizer().lemmatize(text)
    return text

df['tweet'] = df['tweet'].apply(preprocess_text)

# Split data into features and target
X = df['tweet']
y = df['label']

# Define hyperparameters grid for Random Forest
param_grid_rf = {
    'classifier__n_estimators': [50, 100, 200],
    'classifier__max_depth': [None, 10, 20]
}

# Define hyperparameters grid for Logistic Regression
param_grid_lr = {
    'classifier__C': [0.001, 0.01, 0.1, 1, 10, 100]
}

# Define hyperparameters grid for Support Vector Machine
param_grid_svm = {
    'classifier__C': [0.1, 1, 10],
    'classifier__gamma': ['scale', 'auto']
}

# Define hyperparameters grid for Multinomial Naive Bayes
param_grid_nb = {
    'classifier__alpha': [0.1, 0.5, 1.0]
}

# Initialize KFold cross-validator
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Random Forest
print("Tuning hyperparameters for Random Forest:")
pipeline_rf = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', RandomForestClassifier())
])
grid_search_rf = GridSearchCV(pipeline_rf, param_grid_rf, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_rf.fit(X, y)
best_params_rf = grid_search_rf.best_params_
best_score_rf = grid_search_rf.best_score_
print(f"Best parameters: {best_params_rf}")
print(f"Best cross-validation accuracy: {best_score_rf}\n")

# Logistic Regression
print("Tuning hyperparameters for Logistic Regression:")
pipeline_lr = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', LogisticRegression())
])
grid_search_lr = GridSearchCV(pipeline_lr, param_grid_lr, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_lr.fit(X, y)
best_params_lr = grid_search_lr.best_params_
best_score_lr = grid_search_lr.best_score_
print(f"Best parameters: {best_params_lr}")
print(f"Best cross-validation accuracy: {best_score_lr}\n")

# Support Vector Machine
print("Tuning hyperparameters for Support Vector Machine:")
pipeline_svm = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', SVC())
])
grid_search_svm = GridSearchCV(pipeline_svm, param_grid_svm, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_svm.fit(X, y)
best_params_svm = grid_search_svm.best_params_
best_score_svm = grid_search_svm.best_score_
print(f"Best parameters: {best_params_svm}")
print(f"Best cross-validation accuracy: {best_score_svm}\n")

# Multinomial Naive Bayes
print("Tuning hyperparameters for Multinomial Naive Bayes:")
pipeline_nb = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', MultinomialNB())
])
grid_search_nb = GridSearchCV(pipeline_nb, param_grid_nb, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_nb.fit(X, y)
best_params_nb = grid_search_nb.best_params_
best_score_nb = grid_search_nb.best_score_
print(f"Best parameters: {best_params_nb}")
print(f"Best cross-validation accuracy: {best_score_nb}\n")

# Choose the best model
best_model_name = max({
    'Random Forest': best_score_rf,
    'Logistic Regression': best_score_lr,
    'Support Vector Machine': best_score_svm,
    'Multinomial Naive Bayes': best_score_nb
}.items(), key=lambda x: x[1])[0]
best_model = None

if best_model_name == 'Random Forest':
    best_model = grid_search_rf.best_estimator_
elif best_model_name == 'Logistic Regression':
    best_model = grid_search_lr.best_estimator_
elif best_model_name == 'Support Vector Machine':
    best_model = grid_search_svm.best_estimator_
elif best_model_name == 'Multinomial Naive Bayes':
    best_model = grid_search_nb.best_estimator_

# Fit the best model
if best_model:
    best_model.fit(X, y)
    # Predict using the best model
    y_pred = best_model.predict(X)
    # Calculate accuracy
    accuracy = accuracy_score(y, y_pred)
    print("Final Accuracy:", accuracy)

    # Calculate and print confusion matrix and classification report
    cm = confusion_matrix(y, y_pred)
    cr = classification_report(y, y_pred)
    print("Confusion Matrix:")
    print(cm)
    print("Classification Report:")
    print(cr)


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Tuning hyperparameters for Random Forest:
Best parameters: {'classifier__max_depth': None, 'classifier__n_estimators': 200}
Best cross-validation accuracy: 0.6995999999999999

Tuning hyperparameters for Logistic Regression:


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Best parameters: {'classifier__C': 10}
Best cross-validation accuracy: 0.7055

Tuning hyperparameters for Support Vector Machine:
Best parameters: {'classifier__C': 10, 'classifier__gamma': 'scale'}
Best cross-validation accuracy: 0.7144999999999999

Tuning hyperparameters for Multinomial Naive Bayes:
Best parameters: {'classifier__alpha': 0.1}
Best cross-validation accuracy: 0.6957

Final Accuracy: 0.9954
Confusion Matrix:
[[2423    8    1]
 [   4 4966   12]
 [   0   21 2565]]
Classification Report:
              precision    recall  f1-score   support

          -1       1.00      1.00      1.00      2432
           0       0.99      1.00      1.00      4982
           1       0.99      0.99      0.99      2586

    accuracy                           1.00     10000
   macro avg       1.00      0.99      1.00     10000
weighted avg       1.00      1.00      1.00     10000



In [ ]:
#الكود الصح مبدئياً
import numpy as np
import pandas as pd
import re
import string
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split, KFold, GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
import time
from imblearn.over_sampling import RandomOverSampler
from sklearn.pipeline import Pipeline

nltk.download('stopwords')
nltk.download('wordnet')

from google.colab import drive
drive.mount('/content/drive')

# قراءة ملف CSV باستخدام Pandas
df = pd.read_csv('/content/drive/MyDrive/train (1).csv')
df  # إظهار البيانات

# Preprocess text column
def preprocess_text(text):
    text = text.lower()
    text = re.sub('@[^\s]+', ' ', text)
    text = re.sub('((www\.[^\s]+)|(https?://[^\s]+))', ' ', text)
    text = re.sub(f'[{string.punctuation}]', ' ', text)
    text = re.sub('[0-9]+', '', text)
    text = " ".join(str(text).split())
    text = [w for w in text.split() if w not in stopwords.words('english')]
    text = " ".join(text)
    text = WordNetLemmatizer().lemmatize(text)
    return text

df['tweet'] = df['tweet'].apply(preprocess_text)

# Split data into features and target
X = df['tweet']
y = df['label']

# Define hyperparameters grid for Random Forest
param_grid_rf = {
    'classifier__n_estimators': [50, 100, 200],
    'classifier__max_depth': [None, 10, 20]
}

# Define hyperparameters grid for Logistic Regression
param_grid_lr = {
    'classifier__C': [0.001, 0.01, 0.1, 1, 10, 100]
}

# Define hyperparameters grid for Support Vector Machine
param_grid_svm = {
    'classifier__C': [0.1, 1, 10],
    'classifier__gamma': ['scale', 'auto']
}

# Define hyperparameters grid for Multinomial Naive Bayes
param_grid_nb = {
    'classifier__alpha': [0.1, 0.5, 1.0]
}

# Initialize KFold cross-validator
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Function to display results in a DataFrame
def display_results(results):
    df_results = pd.DataFrame(results)
    display(df_results)

# Initialize an empty list to store results
results = []

# Random Forest
print("Tuning hyperparameters for Random Forest:")
pipeline_rf = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', RandomForestClassifier())
])
grid_search_rf = GridSearchCV(pipeline_rf, param_grid_rf, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_rf.fit(X, y)
best_params_rf = grid_search_rf.best_params_
best_score_rf = grid_search_rf.best_score_
results.append({'Model': 'Random Forest', 'Best Parameters': best_params_rf, 'Best Cross-validation Accuracy': best_score_rf})

# Logistic Regression
print("Tuning hyperparameters for Logistic Regression:")
pipeline_lr = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', LogisticRegression())
])
grid_search_lr = GridSearchCV(pipeline_lr, param_grid_lr, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_lr.fit(X, y)
best_params_lr = grid_search_lr.best_params_
best_score_lr = grid_search_lr.best_score_
results.append({'Model': 'Logistic Regression', 'Best Parameters': best_params_lr, 'Best Cross-validation Accuracy': best_score_lr})

# Support Vector Machine
print("Tuning hyperparameters for Support Vector Machine:")
pipeline_svm = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', SVC())
])
grid_search_svm = GridSearchCV(pipeline_svm, param_grid_svm, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_svm.fit(X, y)
best_params_svm = grid_search_svm.best_params_
best_score_svm = grid_search_svm.best_score_
results.append({'Model': 'Support Vector Machine', 'Best Parameters': best_params_svm, 'Best Cross-validation Accuracy': best_score_svm})

# Multinomial Naive Bayes
print("Tuning hyperparameters for Multinomial Naive Bayes:")
pipeline_nb = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', MultinomialNB())
])
grid_search_nb = GridSearchCV(pipeline_nb, param_grid_nb, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_nb.fit(X, y)
best_params_nb = grid_search_nb.best_params_
best_score_nb = grid_search_nb.best_score_
results.append({'Model': 'Multinomial Naive Bayes', 'Best Parameters': best_params_nb, 'Best Cross-validation Accuracy': best_score_nb})

# Display results
display_results(results)


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Tuning hyperparameters for Random Forest:
Tuning hyperparameters for Logistic Regression:


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Tuning hyperparameters for Support Vector Machine:
Tuning hyperparameters for Multinomial Naive Bayes:


Model                                    Best Parameters  \
0            Random Forest  {'classifier__max_depth': None, 'classifier__n...   
1      Logistic Regression                              {'classifier__C': 10}   
2   Support Vector Machine  {'classifier__C': 10, 'classifier__gamma': 'sc...   
3  Multinomial Naive Bayes                         {'classifier__alpha': 0.1}   

   Best Cross-validation Accuracy  
0                          0.6981  
1                          0.7055  
2                          0.7145  
3                          0.6957

In [ ]:
#using model from hugging face
import numpy as np
import pandas as pd
import re
import string
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split, KFold, GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
import time
from imblearn.over_sampling import RandomOverSampler
from sklearn.pipeline import Pipeline

nltk.download('stopwords')
nltk.download('wordnet')

from transformers import pipeline

from google.colab import drive
drive.mount('/content/drive')

# Read the CSV file using Pandas
df = pd.read_csv('/content/drive/MyDrive/train (1).csv')
print(df.head())  # Display the data

# Preprocess the text column
def preprocess_text(text):
    text = text.lower()
    text = re.sub('@[^\s]+', ' ', text)
    text = re.sub('((www\.[^\s]+)|(https?://[^\s]+))', ' ', text)
    text = re.sub(f'[{string.punctuation}]', ' ', text)
    text = re.sub('[0-9]+', '', text)
    text = " ".join(str(text).split())
    text = [w for w in text.split() if w not in stopwords.words('english')]
    text = " ".join(text)
    text = WordNetLemmatizer().lemmatize(text)
    return text

df['tweet'] = df['tweet'].apply(preprocess_text)

# Initialize sentiment analysis pipeline
sentiment_pipeline = pipeline("text-classification", model="j-hartmann/sentiment-roberta-large-english-3-classes")

# Apply sentiment analysis to the text column
sentiment_predictions = sentiment_pipeline(df['tweet'].tolist())

# Add the sentiment predictions to the DataFrame
df['sentiment'] = [sent['label'] for sent in sentiment_predictions]

# Split data into features and target
X = df['tweet']
y = df['label']

# Define hyperparameters grid for Random Forest
param_grid_rf = {
    'classifier__n_estimators': [50, 100, 200],
    'classifier__max_depth': [None, 10, 20]
}

# Define hyperparameters grid for Logistic Regression
param_grid_lr = {
    'classifier__C': [0.001, 0.01, 0.1, 1, 10, 100]
}

# Define hyperparameters grid for Support Vector Machine
param_grid_svm = {
    'classifier__C': [0.1, 1, 10],
    'classifier__gamma': ['scale', 'auto']
}

# Define hyperparameters grid for Multinomial Naive Bayes
param_grid_nb = {
    'classifier__alpha': [0.1, 0.5, 1.0]
}

# Initialize KFold cross-validator
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Function to display results in a DataFrame
def display_results(results):
    df_results = pd.DataFrame(results)
    display(df_results)

# Initialize an empty list to store results
results = []

# Random Forest
print("Tuning hyperparameters for Random Forest:")
pipeline_rf = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', RandomForestClassifier())
])
grid_search_rf = GridSearchCV(pipeline_rf, param_grid_rf, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_rf.fit(X, y)
best_params_rf = grid_search_rf.best_params_
best_score_rf = grid_search_rf.best_score_
results.append({'Model': 'Random Forest', 'Best Parameters': best_params_rf, 'Best Cross-validation Accuracy': best_score_rf})

# Logistic Regression
print("Tuning hyperparameters for Logistic Regression:")
pipeline_lr = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', LogisticRegression())
])
grid_search_lr = GridSearchCV(pipeline_lr, param_grid_lr, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_lr.fit(X, y)
best_params_lr = grid_search_lr.best_params_
best_score_lr = grid_search_lr.best_score_
results.append({'Model': 'Logistic Regression', 'Best Parameters': best_params_lr, 'Best Cross-validation Accuracy': best_score_lr})

# Support Vector Machine
print("Tuning hyperparameters for Support Vector Machine:")
pipeline_svm = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', SVC())
])
grid_search_svm = GridSearchCV(pipeline_svm, param_grid_svm, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_svm.fit(X, y)
best_params_svm = grid_search_svm.best_params_
best_score_svm = grid_search_svm.best_score_
results.append({'Model': 'Support Vector Machine', 'Best Parameters': best_params_svm, 'Best Cross-validation Accuracy': best_score_svm})

# Multinomial Naive Bayes
print("Tuning hyperparameters for Multinomial Naive Bayes:")
pipeline_nb = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', MultinomialNB())
])
grid_search_nb = GridSearchCV(pipeline_nb, param_grid_nb, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_nb.fit(X, y)
best_params_nb = grid_search_nb.best_params_
best_score_nb = grid_search_nb.best_score_
results.append({'Model': 'Multinomial Naive Bayes', 'Best Parameters': best_params_nb, 'Best Cross-validation Accuracy': best_score_nb})

# Display results
display_results(results)


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...


Mounted at /content/drive
                                               tweet  label
0  BofA previews Netflixs NFLX Q3 Earnings Tues 0...      0
1  I scooped a couple of shares this morning at a...      0
2  Im streaming ES Futures using Bookmap on youtu...      0
3             CF taking some off here close to 19150      1
4  No change to this position is still bullish st...      0


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/725 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.43G [00:00<?, ?B/s]

...

/usr/local/lib/python3.10/dist-packages/joblib/externals/loky/backend/fork_exec.py:38: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  pid = os.fork()


Tuning hyperparameters for Logistic Regression:


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Tuning hyperparameters for Support Vector Machine:
Tuning hyperparameters for Multinomial Naive Bayes:


Model                                    Best Parameters  \
0            Random Forest  {'classifier__max_depth': None, 'classifier__n...   
1      Logistic Regression                              {'classifier__C': 10}   
2   Support Vector Machine  {'classifier__C': 10, 'classifier__gamma': 'sc...   
3  Multinomial Naive Bayes                         {'classifier__alpha': 0.1}   

   Best Cross-validation Accuracy  
0                          0.6981  
1                          0.7055  
2                          0.7145  
3                          0.6957

In [ ]:
#تعديل على الكود #using model from hugging face

# Libraries
import numpy as np
import pandas as pd
import re
import string
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split, KFold, GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
import time
from imblearn.over_sampling import RandomOverSampler
from sklearn.pipeline import Pipeline

nltk.download('stopwords')
nltk.download('wordnet')

from transformers import pipeline

from google.colab import drive
drive.mount('/content/drive')

# Read CSV file
df = pd.read_csv('/content/drive/MyDrive/train (1).csv')
print(df.head())  # Display the data

# Preprocess text function
def preprocess_text(text):
    text = text.lower()
    text = re.sub('@[^\s]+', ' ', text)
    text = re.sub('((www\.[^\s]+)|(https?://[^\s]+))', ' ', text)
    text = re.sub(f'[{string.punctuation}]', ' ', text)
    text = re.sub('[0-9]+', '', text)
    text = " ".join(str(text).split())
    text = [w for w in text.split() if w not in stopwords.words('english')]
    text = " ".join(text)
    text = WordNetLemmatizer().lemmatize(text)
    return text

df['tweet'] = df['tweet'].apply(preprocess_text)

# Split data into features and target (avoiding data leakage)
X_train, X_test, y_train, y_test = train_test_split(df['tweet'], df['label'], test_size=0.2, random_state=42)

# Initialize KFold cross-validator
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Function to display results in a DataFrame
def display_results(results):
    df_results = pd.DataFrame(results)
    print(df_results)

# Initialize an empty list to store results
results = []

# Define hyperparameters grid for Random Forest
param_grid_rf = {
  'classifier__n_estimators': [50, 100, 200],
  'classifier__max_depth': [None, 10, 20]
}

# Define hyperparameters grid for Logistic Regression
param_grid_lr = {
  'classifier__C': [0.001, 0.01, 0.1, 1, 10, 100]
}

# Define hyperparameters grid for Support Vector Machine
param_grid_svm = {
  'classifier__C': [0.1, 1, 10],
  'classifier__gamma': ['scale', 'auto']
}

# Define hyperparameters grid for Multinomial Naive Bayes
param_grid_nb = {
  'classifier__alpha': [0.1, 0.5, 1.0]
}

# Random Forest
print("Tuning hyperparameters for Random Forest:")
pipeline_rf = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', RandomForestClassifier())
])
grid_search_rf = GridSearchCV(pipeline_rf, param_grid_rf, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_rf.fit(X_train, y_train)
best_params_rf = grid_search_rf.best_params_
best_score_rf = grid_search_rf.best_score_
results.append({'Model': 'Random Forest', 'Best Parameters': best_params_rf, 'Best Cross-validation Accuracy': best_score_rf})

# Logistic Regression
print("Tuning hyperparameters for Logistic Regression:")
pipeline_lr = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', LogisticRegression())
])
grid_search_lr = GridSearchCV(pipeline_lr, param_grid_lr, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_lr.fit(X_train, y_train)
best_params_lr = grid_search_lr.best_params_
best_score_lr = grid_search_lr.best_score_
results.append({'Model': 'Logistic Regression', 'Best Parameters': best_params_lr, 'Best Cross-validation Accuracy': best_score_lr})

# Support Vector Machine
print("Tuning hyperparameters for Support Vector Machine:")
pipeline_svm = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', SVC())
])
grid_search_svm = GridSearchCV(pipeline_svm, param_grid_svm, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_svm.fit(X_train, y_train)
best_params_svm = grid_search_svm.best_params_
best_score_svm = grid_search_svm.best_score_
results.append({'Model': 'Support Vector Machine', 'Best Parameters': best_params_svm, 'Best Cross-validation Accuracy': best_score_svm})

# Multinomial Naive Bayes
print("Tuning hyperparameters for Multinomial Naive Bayes:")
pipeline_nb = Pipeline([
    ('tfidf', TfidfVectorizer()),
    ('classifier', MultinomialNB())
])
grid_search_nb = GridSearchCV(pipeline_nb, param_grid_nb, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_nb.fit(X_train, y_train)
best_params_nb = grid_search_nb.best_params_
best_score_nb = grid_search_nb.best_score_
results.append({'Model': 'Multinomial Naive Bayes', 'Best Parameters': best_params_nb, 'Best Cross-validation Accuracy': best_score_nb})

# Display results
display_results(results)

# Evaluate on test data (including additional metrics)
print("Performance on Test Set:")
for model_name, model in [('Random Forest', grid_search_rf), ('Logistic Regression', grid_search_lr), ('Support Vector Machine', grid_search_svm), ('Multinomial Naive Bayes', grid_search_nb)]:
  y_pred = model.predict(X_test)
  print(f"Model: {model_name}")
  print(classification_report(y_test, y_pred))
  print(confusion_matrix(y_test, y_pred))


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
                                               tweet  label
0  BofA previews Netflixs NFLX Q3 Earnings Tues 0...      0
1  I scooped a couple of shares this morning at a...      0
2  Im streaming ES Futures using Bookmap on youtu...      0
3             CF taking some off here close to 19150      1
4  No change to this position is still bullish st...      0
Tuning hyperparameters for Random Forest:


/usr/local/lib/python3.10/dist-packages/joblib/externals/loky/backend/fork_exec.py:38: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  pid = os.fork()


Tuning hyperparameters for Logistic Regression:


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Tuning hyperparameters for Support Vector Machine:
Tuning hyperparameters for Multinomial Naive Bayes:
                     Model                                    Best Parameters  \
0            Random Forest  {'classifier__max_depth': None, 'classifier__n...   
1      Logistic Regression                              {'classifier__C': 10}   
2   Support Vector Machine  {'classifier__C': 10, 'classifier__gamma': 'sc...   
3  Multinomial Naive Bayes                         {'classifier__alpha': 0.1}   

   Best Cross-validation Accuracy  
0                        0.691000  
1                        0.698375  
2                        0.707000  
3                        0.689750  
Performance on Test Set:
Model: Random Forest
              precision    recall  f1-score   support

          -1       0.70      0.51      0.59       512
           0       0.68      0.86      0.76       985
           1       0.78      0.58      0.67       503

    accuracy                           0.70    

In [ ]:
import numpy as np
import pandas as pd
import re
import string
import nltk
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.model_selection import train_test_split, KFold, GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score
from imblearn.over_sampling import RandomOverSampler
from sklearn.pipeline import Pipeline

from google.colab import drive
drive.mount('/content/drive')

# قراءة ملف CSV باستخدام Pandas
df = pd.read_csv('/content/drive/MyDrive/train (1).csv')

# Preprocess text column
def preprocess_text(text):
    text = text.lower()
    text = re.sub('@[^\s]+', ' ', text)
    text = re.sub('((www\.[^\s]+)|(https?://[^\s]+))', ' ', text)
    text = re.sub(f'[{string.punctuation}]', ' ', text)
    text = re.sub('[0-9]+', '', text)
    text = " ".join(str(text).split())
    text = [w for w in text.split() if w not in stopwords.words('english')]
    text = " ".join(text)
    text = WordNetLemmatizer().lemmatize(text)
    return text

df['tweet'] = df['tweet'].apply(preprocess_text)

# Split data into features and target
X = df['tweet']
y = df['label']

# Initialize RandomForestClassifier
rf = RandomForestClassifier()

# Define hyperparameters grid
param_grid = {
    'rf__n_estimators': [50, 100, 200],
    'rf__max_depth': [None, 10, 20],
}

# Initialize KFold cross-validator
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Define pipeline
pipeline = Pipeline([
    ('vectorizer', TfidfVectorizer()),
    ('rf', rf)
])

# Perform hyperparameter tuning
grid_search = GridSearchCV(pipeline, param_grid, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search.fit(X, y)

# Get best model and parameters
best_model = grid_search.best_estimator_
best_params = grid_search.best_params_
best_score = grid_search.best_score_

print("Best parameters:", best_params)
print("Best cross-validation accuracy:", best_score)

# Fit the best model
best_model.fit(X, y)

# Predict using the best model
y_pred = best_model.predict(X)

# Calculate accuracy
accuracy = accuracy_score(y, y_pred)
print("Final Accuracy:", accuracy)


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Best parameters: {'rf__max_depth': None, 'rf__n_estimators': 200}
Best cross-validation accuracy: 0.6987
Final Accuracy: 0.9955


In [ ]:
#بدون معالجة
# Libraries
import numpy as np
import pandas as pd
import re
import string
import nltk
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split, KFold, GridSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
import time
from imblearn.over_sampling import RandomOverSampler
from sklearn.pipeline import Pipeline

nltk.download('stopwords')

from google.colab import drive
drive.mount('/content/drive')

# Read CSV file
df = pd.read_csv('/content/drive/MyDrive/train (1).csv')
print(df.head())  # Display the data

# Split data into features and target (avoiding data leakage)
X_train, X_test, y_train, y_test = train_test_split(df['tweet'], df['label'], test_size=0.2, random_state=42)

# Initialize KFold cross-validator
kf = KFold(n_splits=5, shuffle=True, random_state=42)

# Function to display results in a DataFrame
def display_results(results):
    df_results = pd.DataFrame(results)
    print(df_results)

# Initialize an empty list to store results
results = []

# Define hyperparameters grid for Random Forest
param_grid_rf = {
  'classifier__n_estimators': [50, 100, 200],
  'classifier__max_depth': [None, 10, 20]
}

# Define hyperparameters grid for Logistic Regression
param_grid_lr = {
  'classifier__C': [0.001, 0.01, 0.1, 1, 10, 100]
}

# Define hyperparameters grid for Support Vector Machine
param_grid_svm = {
  'classifier__C': [0.1, 1, 10],
  'classifier__gamma': ['scale', 'auto']
}

# Define hyperparameters grid for Multinomial Naive Bayes
param_grid_nb = {
  'classifier__alpha': [0.1, 0.5, 1.0]
}

# Random Forest
print("Tuning hyperparameters for Random Forest:")
pipeline_rf = Pipeline([
    ('tfidf', TfidfVectorizer(stop_words=stopwords.words('english'))),
    ('classifier', RandomForestClassifier())
])
grid_search_rf = GridSearchCV(pipeline_rf, param_grid_rf, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_rf.fit(X_train, y_train)
best_params_rf = grid_search_rf.best_params_
best_score_rf = grid_search_rf.best_score_
results.append({'Model': 'Random Forest', 'Best Parameters': best_params_rf, 'Best Cross-validation Accuracy': best_score_rf})

# Logistic Regression
print("Tuning hyperparameters for Logistic Regression:")
pipeline_lr = Pipeline([
    ('tfidf', TfidfVectorizer(stop_words=stopwords.words('english'))),
    ('classifier', LogisticRegression())
])
grid_search_lr = GridSearchCV(pipeline_lr, param_grid_lr, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_lr.fit(X_train, y_train)
best_params_lr = grid_search_lr.best_params_
best_score_lr = grid_search_lr.best_score_
results.append({'Model': 'Logistic Regression', 'Best Parameters': best_params_lr, 'Best Cross-validation Accuracy': best_score_lr})

# Support Vector Machine
print("Tuning hyperparameters for Support Vector Machine:")
pipeline_svm = Pipeline([
    ('tfidf', TfidfVectorizer(stop_words=stopwords.words('english'))),
    ('classifier', SVC())
])
grid_search_svm = GridSearchCV(pipeline_svm, param_grid_svm, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_svm.fit(X_train, y_train)
best_params_svm = grid_search_svm.best_params_
best_score_svm = grid_search_svm.best_score_
results.append({'Model': 'Support Vector Machine', 'Best Parameters': best_params_svm, 'Best Cross-validation Accuracy': best_score_svm})

# Multinomial Naive Bayes
print("Tuning hyperparameters for Multinomial Naive Bayes:")
pipeline_nb = Pipeline([
    ('tfidf', TfidfVectorizer(stop_words=stopwords.words('english'))),
    ('classifier', MultinomialNB())
])
grid_search_nb = GridSearchCV(pipeline_nb, param_grid_nb, cv=kf, scoring='accuracy', n_jobs=-1)
grid_search_nb.fit(X_train, y_train)
best_params_nb = grid_search_nb.best_params_
best_score_nb = grid_search_nb.best_score_
results.append({'Model': 'Multinomial Naive Bayes', 'Best Parameters': best_params_nb, 'Best Cross-validation Accuracy': best_score_nb})

# Display results
display_results(results)

# Evaluate on test data (including additional metrics)
print("Performance on Test Set:")
for model_name, model in [('Random Forest', grid_search_rf), ('Logistic Regression', grid_search_lr), ('Support Vector Machine', grid_search_svm), ('Multinomial Naive Bayes', grid_search_nb)]:
  y_pred = model.predict(X_test)
  print(f"Model: {model_name}")
  print(classification_report(y_test, y_pred))
  print(confusion_matrix(y_test, y_pred))



[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
                                               tweet  label
0  BofA previews Netflixs NFLX Q3 Earnings Tues 0...      0
1  I scooped a couple of shares this morning at a...      0
2  Im streaming ES Futures using Bookmap on youtu...      0
3             CF taking some off here close to 19150      1
4  No change to this position is still bullish st...      0
Tuning hyperparameters for Random Forest:
Tuning hyperparameters for Logistic Regression:


/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


Tuning hyperparameters for Support Vector Machine:
Tuning hyperparameters for Multinomial Naive Bayes:
                     Model                                    Best Parameters  \
0            Random Forest  {'classifier__max_depth': None, 'classifier__n...   
1      Logistic Regression                              {'classifier__C': 10}   
2   Support Vector Machine  {'classifier__C': 10, 'classifier__gamma': 'sc...   
3  Multinomial Naive Bayes                         {'classifier__alpha': 0.1}   

   Best Cross-validation Accuracy  
0                        0.686875  
1                        0.700625  
2                        0.705000  
3                        0.695625  
Performance on Test Set:
Model: Random Forest
              precision    recall  f1-score   support

          -1       0.71      0.51      0.59       512
           0       0.68      0.87      0.76       985
           1       0.76      0.56      0.64       503

    accuracy                           0.70    